In [1]:
# Change the dataset in global_vars.py to UKB.
from global_vars import *
from commons import *

import glob 
import os

one_time_n4_optimization = True
vol_to_check_list = None #['1942395_20201_2_0'] #['']
exclude = ['1004985_20201_2_0']
# 1018320_20201_2_0, 988, test:no-gallbladder=1108214_20201_2_0
%load_ext autoreload
%autoreload 2

In [2]:
data_dir

'/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti'

In [3]:
def load_ukb_file_paths(load_from_txt_file=True):
    volumes_to_use = []
    if load_from_txt_file:
        with open(volume_txt_file) as file_handle:
                volumes_to_use = file_handle.read().splitlines()
    else:
        volumes_to_use = [name for name in os.listdir(data_dir)]

    file_paths = {}
    
    for vol in volumes_to_use:
        if (vol_to_check_list is not None and vol not in vol_to_check_list) or (vol == "") or (vol in exclude):
            continue
            
        opp_paths = glob.glob(f'{data_dir}/{vol}/**opp**_[17s, 17sa,17sb]**.nii.gz')
        in_paths = glob.glob(f'{data_dir}/{vol}/**in**_[17s,17sa,17sb]**.nii.gz')
        f_paths = glob.glob(f'{data_dir}/{vol}/**F**_[17s, 17sa,17sb]**.nii.gz')
        w_paths = glob.glob(f'{data_dir}/{vol}/**W**_[17s, 17sa,17sb]**.nii.gz')
        
        labelmap_paths = glob.glob(f'{label_dir}/{vol}/**')
        
        vol_madals_paths = dict(
        OPP=opp_paths,
        IN=in_paths,
        F=f_paths,
        W=w_paths
        )
        file_paths[str(vol)]=dict(
            VOLUME_PATHS=vol_madals_paths,
            LABEL_PATHS=labelmap_paths,
        )
    return file_paths

file_paths = load_ukb_file_paths()
file_paths

{'1000410_20201_2_0': {'VOLUME_PATHS': {'OPP': ['/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_opp_Dixon_BH_17s.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_opp_Dixon_BH_17sa.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_opp_Dixon_BH_17sb.nii.gz'],
   'IN': ['/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_in_Dixon_BH_17s_e2.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_in_Dixon_BH_17s_e2a.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_in_Dixon_BH_17s_e2b.nii.gz'],
   'F': ['/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_F_Dixon_BH_17s.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/body/body_nifti/1000410_20201_2_0/Dixon_BH_17s_F_Dixon_BH_17sa.nii.gz',
    '/mnt/nas/Data_WholeBody/UKBiobank/b

In [4]:
# Individual RESCALING.
n4_dict = {}
for vol in file_paths.keys():
    if one_time_n4_optimization:
        break
    if vol_to_check_list is not None and vol not in vol_to_check_list:
        continue
    print(f'n4 processing part-1 started with {vol}...')
    n4_dict[vol] = []
    vol_parts = [[file, read_ras(file)] for file in file_paths[vol]['VOLUME_PATHS']['IN']]
    for orig_file, in_image in vol_parts:
        n4_dict[vol].append(rescale(in_image, vol, orig_file))

In [5]:
# SITK does ot work due to differences in pixel resolution of IN and corresponding OPP Scan.
# Only applying once at the end.
for vol in file_paths.keys():
    if one_time_n4_optimization:
        break
    if vol_to_check_list is not None and vol not in vol_to_check_list:
        continue
    print(f'n4-biasfield-correction starting with {vol}...')
    for idx, n4_d in enumerate(n4_dict[vol]):
        in_file = n4_d['SCALED']
        opp_file = file_paths[vol]['VOLUME_PATHS']['OPP'][idx]
        new_filename = opp_file.split('/')[-1].split('.')[0]
        output_file = f'{n4_corrected_data_dir}/vol/{vol}/{new_filename}_n4_corrected_sitk.nii.gz'
        SITK_N4_normalization(in_file, opp_file, output_file)
        n4_dict[vol][idx]['OPP_CORRECTED'] = output_file

    file_paths[vol]['N4_1'] = n4_dict[vol]

In [6]:
# STITCHING VOL PARTS HERE
for vol in file_paths.keys():
    try:
        print(f'started with {vol}...')
        if vol_to_check_list is not None and vol not in vol_to_check_list:
            continue
        create_if_not(f'{n4_corrected_data_dir}/vol/{vol}')
        file_paths[vol]['ONE'] = {}
        for modality_key in file_paths[vol]['VOLUME_PATHS'].keys():
            print(f"processing {modality_key}")
            orig_modal_key = modality_key
            if one_time_n4_optimization:
                vol_parts = [read_ras(file) for file in file_paths[vol]['VOLUME_PATHS'][modality_key]]
            else:
                if modality_key == 'OPP':
                    vol_parts = [read_ras(data_dict['OPP_CORRECTED']) for data_dict in file_paths[vol]['N4_1']]
                    modality_key = modality_key+'_n4_corrected'
                else:
                    vol_parts = [read_ras(file) for file in file_paths[vol]['VOLUME_PATHS'][modality_key]]

            ras_stitched = multi_vol_stitching(vol_parts)
            save_volume(ras_stitched, f'{n4_corrected_data_dir}/vol/{vol}/{modality_key}_ras_stitched')
            file_paths[vol]['ONE'][f'{orig_modal_key}'] = f'{n4_corrected_data_dir}/vol/{vol}/{modality_key}_ras_stitched.nii.gz'
    except Exception as e:
        print('ERROR:', e)
        continue

started with 1000410_20201_2_0...
processing OPP
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.    

0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1000698_20201_2_0
processing W
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.        

0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1000870_20201_2_0
processing F
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.        

0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1002876_20201_2_0
processing IN
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.       

0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1004543_20201_2_0
started with 1004760_20201_2_0...
processing OPP
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.   

...

Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1253121_20201_2_0
processing W
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.       

Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1253464_20201_2_0
processing F
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]


started with 1254247_20201_2_0...
processing OPP
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -462.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.    

0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1254336_20201_2_0
processing W
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.        

Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
0th img for stitching...
1th img for stitching...
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1254884_20201_2_0
processing F
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.         -247.7678833 ]
 [   0.            2.23214293    0.         -191.96429443]
 [   0.            0.            4.5        -294.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (224, 174, 44)
Transforming Images to RAS.....
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.23214293    0.            0.       

In [8]:
# RESCALING INTENSITIES OF STITCHED VOLUME ABOVE 0
n4_dict = {}
for vol in file_paths.keys():
    try:
        if vol_to_check_list is not None and vol not in vol_to_check_list:
            continue
        print(f'n4 processing part-2 started with {vol}...')
        if vol_to_check_list is not None and vol not in vol_to_check_list:
            continue
        n4_dict[vol] = {}
        in_stitched_file_path, in_stitched_img = file_paths[vol]['ONE']['IN'], read_ras(file_paths[vol]['ONE']['IN'])
        n4_dict[vol]['N4_2'] = rescale(in_stitched_img, vol, in_stitched_file_path)
        
    except Exception as e:
        print('ERROR:',e)
        continue

n4 processing part-2 started with 1000410_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-139.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1000410_20201_2_0
n4 processing part-2 started with 1000698_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-131.0
neagtive value detected
saving directo

n4 processing part-2 started with 1007156_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-166.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1007156_20201_2_0
n4 processing part-2 started with 1007400_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-104.0
neagtive value detected
saving directo

n4 processing part-2 started with 1010424_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-151.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1010424_20201_2_0
n4 processing part-2 started with 1010532_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-153.0
neagtive value detected
saving directo

n4 processing part-2 started with 1015918_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-139.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1015918_20201_2_0
n4 processing part-2 started with 1016258_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-148.0
neagtive value detected
saving directo

n4 processing part-2 started with 1020371_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-111.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1020371_20201_2_0
n4 processing part-2 started with 1020508_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-92.0
neagtive value detected
saving director

...

n4 processing part-2 started with 1236123_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-170.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1236123_20201_2_0
n4 processing part-2 started with 1236217_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-156.0
neagtive value detected
saving directo

n4 processing part-2 started with 1240681_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-165.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1240681_20201_2_0
n4 processing part-2 started with 1240772_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-101.0
neagtive value detected
saving directo

n4 processing part-2 started with 1245015_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-163.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1245015_20201_2_0
n4 processing part-2 started with 1245096_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-120.0
neagtive value detected
saving directo

n4 processing part-2 started with 1248688_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-102.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1248688_20201_2_0
n4 processing part-2 started with 1249799_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-107.0
neagtive value detected
saving directo

n4 processing part-2 started with 1252545_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-127.0
neagtive value detected
saving directory: /mnt/nas/Abhijit/Jyotirmay/abdominal_segmentation/temp/UKB/n4_corrected_2/vol/1252545_20201_2_0
n4 processing part-2 started with 1252605_20201_2_0...
Reading Files.....
Reading Nifti Files.....
Affine:[[   2.            0.            0.         -247.7678833 ]
 [   0.            2.            0.         -191.96429443]
 [   0.            0.            3.         -630.75      ]
 [   0.            0.            0.            1.        ]], Image Shape: (250, 195, 178)
Transforming Images to RAS.....
-165.0
neagtive value detected
saving directo

In [9]:
for vol in file_paths.keys():
    try:
        if vol_to_check_list is not None and vol not in vol_to_check_list:
            continue
        print(f'n4-biasfield-correction starting with {vol}...')
        in_file = n4_dict[vol]['N4_2']['SCALED']
        opp_file = file_paths[vol]['ONE']['OPP']
        new_filename = opp_file.split('/')[-1].split('.')[0]
        output_file = f'{n4_corrected_data_dir}/vol/{vol}/{new_filename}_n4_corrected_sitk.nii.gz'
        SITK_N4_normalization(in_file, opp_file, output_file)
        n4_dict[vol]['N4_2']['OPP_CORRECTED'] = output_file
        file_paths[vol]['N4_2'] = n4_dict[vol]['N4_2']
        
    except Exception as e:
        print('ERROR:',e)
        continue

n4-biasfield-correction starting with 1000410_20201_2_0...
done
n4-biasfield-correction starting with 1000698_20201_2_0...
done
n4-biasfield-correction starting with 1000857_20201_2_0...
done
n4-biasfield-correction starting with 1000870_20201_2_0...
done
n4-biasfield-correction starting with 1002272_20201_2_0...
done
n4-biasfield-correction starting with 1002876_20201_2_0...
done
n4-biasfield-correction starting with 1004543_20201_2_0...
done
n4-biasfield-correction starting with 1004760_20201_2_0...
done
n4-biasfield-correction starting with 1005188_20201_2_0...
done
n4-biasfield-correction starting with 1005645_20201_2_0...
done
n4-biasfield-correction starting with 1005691_20201_2_0...
done
n4-biasfield-correction starting with 1006276_20201_2_0...
done
n4-biasfield-correction starting with 1006486_20201_2_0...
done
n4-biasfield-correction starting with 1006931_20201_2_0...
done
n4-biasfield-correction starting with 1007005_20201_2_0...
done
n4-biasfield-correction starting with 10

done
n4-biasfield-correction starting with 1040016_20201_2_0...
done
n4-biasfield-correction starting with 1040436_20201_2_0...
done
n4-biasfield-correction starting with 1040463_20201_2_0...
done
n4-biasfield-correction starting with 1040640_20201_2_0...
done
n4-biasfield-correction starting with 1041148_20201_2_0...
done
n4-biasfield-correction starting with 1041591_20201_2_0...
done
n4-biasfield-correction starting with 1041786_20201_2_0...
done
n4-biasfield-correction starting with 1041806_20201_2_0...
done
n4-biasfield-correction starting with 1042398_20201_2_0...
done
n4-biasfield-correction starting with 1042468_20201_2_0...
done
n4-biasfield-correction starting with 1042549_20201_2_0...
done
n4-biasfield-correction starting with 1042710_20201_2_0...
done
n4-biasfield-correction starting with 1043311_20201_2_0...
done
n4-biasfield-correction starting with 1043419_20201_2_0...
done
n4-biasfield-correction starting with 1043460_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1070547_20201_2_0...
done
n4-biasfield-correction starting with 1070775_20201_2_0...
done
n4-biasfield-correction starting with 1070854_20201_2_0...
done
n4-biasfield-correction starting with 1071263_20201_2_0...
done
n4-biasfield-correction starting with 1071364_20201_2_0...
done
n4-biasfield-correction starting with 1071396_20201_2_0...
done
n4-biasfield-correction starting with 1072146_20201_2_0...
done
n4-biasfield-correction starting with 1072380_20201_2_0...
done
n4-biasfield-correction starting with 1072410_20201_2_0...
done
n4-biasfield-correction starting with 1072434_20201_2_0...
done
n4-biasfield-correction starting with 1072590_20201_2_0...
done
n4-biasfield-correction starting with 1072665_20201_2_0...
done
n4-biasfield-correction starting with 1073055_20201_2_0...
done
n4-biasfield-correction starting with 1073061_20201_2_0...
done
n4-biasfield-correction starting with 1073305_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1101255_20201_2_0...
done
n4-biasfield-correction starting with 1101562_20201_2_0...
done
n4-biasfield-correction starting with 1101763_20201_2_0...
done
n4-biasfield-correction starting with 1101780_20201_2_0...
done
n4-biasfield-correction starting with 1102206_20201_2_0...
done
n4-biasfield-correction starting with 1103280_20201_2_0...
done
n4-biasfield-correction starting with 1103457_20201_2_0...
done
n4-biasfield-correction starting with 1103793_20201_2_0...
done
n4-biasfield-correction starting with 1103855_20201_2_0...
done
n4-biasfield-correction starting with 1104004_20201_2_0...
done
n4-biasfield-correction starting with 1104082_20201_2_0...
done
n4-biasfield-correction starting with 1104354_20201_2_0...
done
n4-biasfield-correction starting with 1104387_20201_2_0...
done
n4-biasfield-correction starting with 1104606_20201_2_0...
done
n4-biasfield-correction starting with 1104788_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1131794_20201_2_0...
done
n4-biasfield-correction starting with 1132209_20201_2_0...
done
n4-biasfield-correction starting with 1132217_20201_2_0...
done
n4-biasfield-correction starting with 1132291_20201_2_0...
done
n4-biasfield-correction starting with 1132331_20201_2_0...
done
n4-biasfield-correction starting with 1132516_20201_2_0...
done
n4-biasfield-correction starting with 1132520_20201_2_0...
done
n4-biasfield-correction starting with 1132985_20201_2_0...
done
n4-biasfield-correction starting with 1133135_20201_2_0...
done
n4-biasfield-correction starting with 1133172_20201_2_0...
done
n4-biasfield-correction starting with 1133310_20201_2_0...
done
n4-biasfield-correction starting with 1133475_20201_2_0...
done
n4-biasfield-correction starting with 1133593_20201_2_0...
done
n4-biasfield-correction starting with 1133720_20201_2_0...
done
n4-biasfield-correction starting with 1134453_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1164666_20201_2_0...
done
n4-biasfield-correction starting with 1164714_20201_2_0...
done
n4-biasfield-correction starting with 1164795_20201_2_0...
done
n4-biasfield-correction starting with 1164934_20201_2_0...
done
n4-biasfield-correction starting with 1165124_20201_2_0...
done
n4-biasfield-correction starting with 1165138_20201_2_0...
done
n4-biasfield-correction starting with 1165169_20201_2_0...
done
n4-biasfield-correction starting with 1165288_20201_2_0...
done
n4-biasfield-correction starting with 1165374_20201_2_0...
done
n4-biasfield-correction starting with 1165461_20201_2_0...
done
n4-biasfield-correction starting with 1166040_20201_2_0...
done
n4-biasfield-correction starting with 1166295_20201_2_0...
done
n4-biasfield-correction starting with 1166372_20201_2_0...
done
n4-biasfield-correction starting with 1167283_20201_2_0...
done
n4-biasfield-correction starting with 1167473_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1197698_20201_2_0...
done
n4-biasfield-correction starting with 1198000_20201_2_0...
done
n4-biasfield-correction starting with 1198081_20201_2_0...
done
n4-biasfield-correction starting with 1198209_20201_2_0...
done
n4-biasfield-correction starting with 1198793_20201_2_0...
done
n4-biasfield-correction starting with 1198826_20201_2_0...
done
n4-biasfield-correction starting with 1198906_20201_2_0...
done
n4-biasfield-correction starting with 1199413_20201_2_0...
done
n4-biasfield-correction starting with 1199958_20201_2_0...
done
n4-biasfield-correction starting with 1200153_20201_2_0...
done
n4-biasfield-correction starting with 1200228_20201_2_0...
done
n4-biasfield-correction starting with 1200832_20201_2_0...
done
n4-biasfield-correction starting with 1201052_20201_2_0...
done
n4-biasfield-correction starting with 1202059_20201_2_0...
done
n4-biasfield-correction starting with 1202322_20201_2_0...
done
n4-biasfield-correction starting wi

done
n4-biasfield-correction starting with 1232232_20201_2_0...
done
n4-biasfield-correction starting with 1232408_20201_2_0...
done
n4-biasfield-correction starting with 1233030_20201_2_0...
done
n4-biasfield-correction starting with 1233698_20201_2_0...
done
n4-biasfield-correction starting with 1233948_20201_2_0...
done
n4-biasfield-correction starting with 1234011_20201_2_0...
done
n4-biasfield-correction starting with 1234090_20201_2_0...
done
n4-biasfield-correction starting with 1234488_20201_2_0...
done
n4-biasfield-correction starting with 1234846_20201_2_0...
done
n4-biasfield-correction starting with 1235127_20201_2_0...
done
n4-biasfield-correction starting with 1235272_20201_2_0...
done
n4-biasfield-correction starting with 1235437_20201_2_0...
done
n4-biasfield-correction starting with 1235713_20201_2_0...
done
n4-biasfield-correction starting with 1235921_20201_2_0...
done
n4-biasfield-correction starting with 1236123_20201_2_0...
done
n4-biasfield-correction starting wi

In [ ]:
def ukb_vol_label_fix(vol, label, use_alternate_approach=False):
    world_shape = np.max(np.array([list(vol.shape), list(label.shape)]), axis=0)
    final_label = np.zeros(tuple(world_shape))
    
    label_affine = label.affinevolume = hist_match(volume)
    vol_affine = vol.affine
    target_affine = vol_affine
    target_header = vol.header

    sx,sy,sz,ex,ey,ez = np.abs(get_points(label, vol))
    labelmap = label.get_fdata()
    
    if not use_alternate_approach:
        final_label[0:sx+ex, 0:sy+ey, sz:ez] = labelmap
    else:
        final_label[0:sx+ex, 0:sy+ey, sz-20:ez-20] = labelmap

    final_label = np.flip(final_label, axis=0)
    final_label = np.flip(final_label, axis=1)
    
    final_label_img = nb.Nifti1Image(final_label, target_affine, target_header)
    
    return vol, final_label_img

def ukb_label_parts(label_parts, reference_labelmap=None):
    stitched_label = None
    mode = 'constant'
    order = 0
    if reference_labelmap is None:
        label_shape = np.max([img.shape for img, _, _ in label_parts], axis=0)
        reference_labelmap = [img for img, _, _ in label_parts if list(img.shape) == list(label_shape)][0]
    else:
        label_shape = reference_labelmap.shape

    stitched_label = np.zeros(label_shape)
    for labelmap_img, lidx, lname in label_parts:
        print(lidx, lname)
        labelmap_img = makeit_3d(labelmap_img)
        labelmap_img = resample_from_to(labelmap_img, [label_shape, reference_labelmap.affine], order=order, mode=mode, cval=0)
        
        sx,sy,sz,ex,ey,ez = np.abs(get_points(labelmap_img, reference_labelmap))
        
        labelmap = labelmap_img.get_fdata()
        labelmap = np.multiply(lidx, labelmap)
        stitched_label[0:ex+sx, 0:ey+sy, 0:ez+sz] += labelmap
        
        print("###############################################################################################") 
        
    labelmap = np.round(stitched_label)
    stitched_labeled_img = nb.Nifti1Image(labelmap, reference_labelmap.affine, reference_labelmap.header)
    
    return stitched_labeled_img

In [ ]:
print("STARTING NAKO LABEL-MAPS.")
print('Reading Label Maps.....')
for vol in file_paths.keys():
    print(vol)
    if vol_to_check_list is not None and vol not in vol_to_check_list:
        continue
    later = None
    print(file_paths[vol]['LABEL_PATHS'])
    if len(file_paths[vol]['LABEL_PATHS']) == 0:
        print(f"#################### ALERT:: NO LABELPATHS IN THE DICTIONARY FOR {vol} #########################")
        continue
        
    volume = nb.load(file_paths[vol]['N4_2']['OPP_CORRECTED'])
#     volume = nb.load(file_paths[vol]['ONE']['OPP'])
    img_ras_list = []
    later = []
    for label_file_to_read in file_paths[vol]['LABEL_PATHS']:
        img_ras, lidx, labelname = read_ras(label_file_to_read, is_label=True)
        if labelname is None or img_ras is None:
            continue
        img_ras = makeit_3d(img_ras)
        print('After 3d confirmed:', img_ras.shape)
        mode='constant'
        img_ras = resample_to_output(img_ras, TARGET_RESOLUTION, order=0, mode=mode, cval=0.0)
        
        if labelname in ['SPLEEN', 'PANCREAS']:
            later.append([img_ras, lidx+LABEL_EXTENSION_FOR_OVERLAP_REMOVAL, labelname])
        else:
            img_ras_list.append([img_ras, lidx+LABEL_EXTENSION_FOR_OVERLAP_REMOVAL, labelname])

    img_ras_list.extend(later)
        
    s_label = ukb_label_parts(img_ras_list)
    s_label = drop_overlapped_pixels(s_label, np.array(img_ras_list)[:, 1])
    
    if vol == '1004985_20201_2_0':
        volume, s_label = ukb_vol_label_fix(volume, s_label, True)
    else:
        volume, s_label = ukb_vol_label_fix(volume, s_label)
    
    print('Viewing Stitched Images.....')
    volume_3_view_viewer(get_volume_data(volume))
    volume_3_view_viewer(get_volume_data(s_label))

    print('Saving Processed & Stitched Image.....')
    save_volume(volume, f'{processed_dir}/volume/{vol}')
    save_volume(s_label, f'{processed_dir}/label/{vol}')
    print('FINISHED.')
    